In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from itertools import product
plt.style.use("seaborn")

In [ ]:
# WITH OANDA
import tpqoa
api = tpqoa.tpqoa("oandaMY.cfg")

In [ ]:
# WITH IBKR
# ib.disconnect()
import pandas as pd
from ib_insync import *
util.startLoop()  # not necessary in scripts
ib = IB()
ib.connect()

In [ ]:
class SMABacktester():
    ''' Classe per il backtesting di strategie SMA'''
    
    def __init__(self, symbol, SMA_s, SMA_l, start, end):
        '''
        Parametri
        ---------
        symbol: str
            simbolo del ticker per OANDA
        SMA_s: int
            finestra corta
        SMA_l: int
            finestra lunga
        start: str
            data di inizio
        end: str
            data di fine
        '''
        self.symbol = symbol
        self.SMA_s = SMA_s
        self.SMA_l = SMA_l
        self.start = start
        self.end = end
        self.results = None
        self.get_data()
        self.prepare_data()
        
    def __repr__(self):
        return "SMABacktester(symbol = {}, SMA_s = {}, SMA_l = {}, start = {}, end = {})".format(self.symbol,self.SMA_s,
                                                                                self.SMA_l,self.start,self.end)
        
# # WITH OANDA
#     def get_data(self): # carica i dati
#         df = api.get_history(instrument = self.symbol, start = self.start, end = self.end, 
#                              granularity = "D", price = "M")["c"].to_frame()
#         df.rename(columns={"o":"open","h":"high","l":"low","c":"close","time":"date"},inplace=True)
#         df.index.names = ['date']
#         df["logRet"]=np.log(df/df.shift(1))
#         self.data=df.dropna()

# WITH IBKR
    def get_data(self): # carica i dati
        df = pd.DataFrame(ib.reqHistoricalData( self.symbol, endDateTime = self.end, 
                                  barSizeSetting="1 day", durationStr=self.start, 
                                  whatToShow= "MIDPOINT", useRTH = True, formatDate=2 )).set_index("date")
        df.index=pd.to_datetime(df.index)
        df = df.close.to_frame()
        df["logRet"]=np.log(df/df.shift(1))
        self.data=df.dropna()
    
    def prepare_data(self): # contruisce il dataframe internamente 
        self.data["SMA_s"]=self.data["close"].rolling(self.SMA_s).mean()
        self.data["SMA_l"]=self.data["close"].rolling(self.SMA_l).mean()
        # return self.data
    
    def set_parameters(self, SMA_s=None, SMA_l=None):
        if SMA_s is not None:
            self.SMA_s = SMA_s
            self.data["SMA_s"]=self.data["close"].rolling(SMA_s).mean()
        if SMA_l is not None:
            self.SMA_l = SMA_l
            self.data["SMA_l"]=self.data["close"].rolling(SMA_l).mean()

    def test_strategy(self):
        data=self.data.copy()
        data.dropna(inplace=True)
        data["posizione"]=np.where(data.SMA_s>data.SMA_l,+1,-1)
        data["strategia"]= data.posizione.shift(1) * data.logRet
        data.dropna(inplace=True)
        data["cumLogRet"]= data.logRet.cumsum()
        data["cumStrategia"]= data.strategia.cumsum()
        # performance = np.exp(data.cumStrategia.iloc[-1])
        # outPerformance = performance - np.exp(data.cumLogRet.iloc[-1])
        performance = data.cumStrategia.iloc[-1]
        outPerformance = performance - data.cumLogRet.iloc[-1]
        maxDrawdown=(data.strategia.cumsum().cummax()-data.strategia.cumsum()).max()
        self._results=data
        return round(performance,6),round(outPerformance,6),round(maxDrawdown,6)
    
    def plot_results(self):
        if self._results is None:
            print("Devi prima chiamare test_strategy()")
        else:
            titolo="{}    SMA_S = {}     SMA_L = {}".format(self.symbol,self.SMA_s,self.SMA_l)
            self._results[["cumLogRet","cumStrategia"]].plot(figsize=(25,15))
            plt.legend(fontsize=18)
            plt.title(titolo,fontsize=22)
    
    def optimize_parameters(self, SMA_s_range, SMA_l_range): # ranges are tuples
        ''' Trova la stretgia ottimale all\'interno dei range dei parametri indicati
        
        Parametri
        ---------
        SMA_s_range: tuple di 2 o 3 int
            inizio e fine (e eventualmente step) del range per la finestra corta
        SMA_l_range: tuple di 2 o 3 int
            inizio e fine (e eventualmente step) del range per la finestra corta
        '''
        
        combinazioni = list(product(range(SMA_s_range[0],SMA_s_range[1]),range(SMA_l_range[0],SMA_l_range[1]) ))
        # combinazioni = list(product(range(*SMA_s_range),range(*SMA_l_range) ))
        risultati= []
        for comb in combinazioni:
            self.set_parameters(comb[0],comb[1])
            risultati.append(self.test_strategy()[0])
        
        best_performance = np.max(risultati)
        best_combinazione = combinazioni[np.argmax(risultati)]
        
        # eseguiamo la strategia migliore
        self.set_parameters(best_combinazione[0],best_combinazione[1])
        self.test_strategy()
        
        # mettiamo i risulati in un bel dataframe
        AllResults = pd.DataFrame(combinazioni, columns=["SMA_s","SMA_l"])
        AllResults["performance"]= risultati
        self.results_overview = AllResults
        
        return best_combinazione, best_performance
    